In [ ]:
        %matplotlib widget
from IPython.display import display, HTML
display(HTML("<style>.container{width:100% !important;}</style>"))
from random import uniform, seed
from tabulate import tabulate
from numpy import argmax
import numpy as np
from dadk.QUBOSolverCPU import *
import matplotlib.pyplot as plt
import networkx as nx
from random import random

# Optimize Graph Coloring

Graph coloring is a fundamental NP-complete problem with many applications in, e.g., schedule planning and map coloring. 

## Problem and QUBO model
Let $V$ be the set of $N$ vertices and $E$ the set of edges in a given graph. The colors can be chosen from the set $C$, containing $K$ colors. In Graph Coloring we seek a mapping $f: V \to C$ from the set of vertices $V$ into the set of colors $C$ such that for adjacent vertices $v, w \in V$, i.e., $(v,w) \in E$, the vertices have different colors $f(v) \neq f(w)$.

The bit $x_{n,k}=1$ if the vertex $n$ is colored with $k$. The QUBO can then be written as:
$$
H = A H_1 + B H_2 = A \sum_{n=0}^{N-1}\left(1-\sum_{k=0}^{K-1}x_{n,k}\right)^2 + B \sum_{(n,m)\in E}\sum_{k=0}^{K-1}x_{n,k}x_{m,k}
$$


# Exercise: Implement Graph K-Coloring Problem

### Function for Creating Graph Object using Networkx Library

In [ ]:
def create_graph(N:int, edge_prop:float, random_seed:float):
    
    seed(random_seed)
    graph = nx.Graph()     
    for i in range(N):
        graph.add_node(i)
    for i in range(N):
        for j in range(i):
            if random() < edge_prop:
                graph.add_edge(i, j)

    
    N = len(graph.nodes())
    E = len(graph.edges())
        
    print('Graph with %d vertices and %d edges created.' % (N, E))
    return graph

### Create a Graph

In [ ]:
N=20
C=5
graph=create_graph(N,0.4,10)

### Function for creating QUBO Model

In [ ]:
def build_qubo(graph,N,C, A, B):

    var_shape_set = VarShapeSet(BitArrayShape('x', (N, C)))
    BinPol.freeze_var_shape_set(var_shape_set)

    H_1 = BinPol()
    ## YOUR CODE FOR H_1 (First term of the QUBO) GOES HERE 

    ##
    
    # QUBO for different color on adjacent (H_2)
    ## YOUR CODE FOR H_2 (Second term of the QUBO) GOES HERE 

    ##

    # Combine both terms using lagrange terms A and B
    ## YOUR CODE FOR HQ

    ##
    
    return H_1,H_2,HQ

### Creates QUBO Model

In [ ]:
H_1,H_2,HQ=build_qubo(graph,N,C , 5000, 500)

### Solving QUBO Problem

In [ ]:
solver = QUBOSolverCPU(
number_iterations=200000,
number_runs=10,
scaling_bit_precision=32,
auto_tuning=AutoTuning.AUTO_SCALING_AND_SAMPLING)
            
solution_list = solver.minimize(HQ)

print(solution_list.solver_times)

### Function for validating results

In [ ]:
def prep_result(HQ,H_1,H_2 ,solution_list):
    
    solution = solution_list.min_solution
    node_color = solution['x'].data
    
    if C <= 6:
        colors = ['r', 'g', 'b', 'y', 'm', 'c' ]
        jcolors = [0xff0000, 0x00ff00, 0x0000ff, 0xffff00, 0xff00ff, 0x00ffff]
    else:
        r = 1.0 / 3.0
        g = 2.0 / 5.0
        b = 1.0 / 7.0
        base = 0.5
        colors = [(base + (1-base)*(r * i % 1), 
                   base + (1-base)*(g * i % 1), 
                   base + (1-base)*(b * i % 1)) for i in range(C)]
        colors = [(base + (1-base)*(random()), 
                   base + (1-base)*(random()), 
                   base + (1-base)*(random())) for i in range(C)]
        jcolors = [int(2**24 * random()) for i in range(C)]

    def get_color(n):
        found = False
        for c in range(C):
            if node_color[n][c]:
                found = True
                break
        return colors[c] if found else 'w'
    
    colors = [get_color(n) for n in range(N)] 
    violations = [edge for edge in graph.edges if colors[edge[0]]==colors[edge[1]]]
    uncolored = [node for node in range(N) if colors[node]=='w']
    

    print( "HQ  = %10.6f" % (HQ.compute(solution.configuration)) )
    print( "H_1 = %10.6f" % (H_1.compute(solution.configuration)) )
    print( "H_2 = %10.6f" % (H_2.compute(solution.configuration)) )
    return colors,violations,uncolored

### Check the constraints

In [ ]:
colors,violations,uncolored=prep_result(HQ,H_1,H_2 ,solution_list)

### Report the results and plot the solution

In [ ]:
def report(N,C,graph,uncolored,violations):

    print(('Number of colors:      {1:5d}\n' +
           'Number of nodes:       {0:5d}\n' +
           'Number of edges:       {2:5d}\n' +
           'Number of uncolored:   {3:5d}\n' +
           'Uncolored nodes:       {4:s}\n'
           'Number of violations:  {5:5d}\n' +
           'Violations:            {6:s}\n' 
          ).format(N, C, len(graph.edges), 
                   len(uncolored), str(uncolored), 
                   len(violations), str(violations))
         )

def draw(graph,colors):

    if colors is None:
        colors = ['y']*len(graph)
    pos = nx.spring_layout(graph)
    fig = plt.figure(num='Graph (created at %s)' % datetime.now(), figsize=(9.0, 6.0))
    nx.draw(graph, pos=pos, with_labels=True, 
            nodelist=range(len(colors)), node_color=colors)
    plt.show()

In [ ]:
report(N,C,graph,uncolored,violations)

In [ ]:
draw(graph,colors)

## Executing on D-Wave

#### Install all dependencies

In [ ]:
!pip install dimod
!pip install pip-system-certs
!pip install dwave-neal
!pip install dwave-system
!pip install hybrid

### DADK to D-Wave formulation

In [ ]:
# experimental:start
def as_bqm(self) -> 'dimod.BinaryQuadraticModel':
    """
    The polynomial is returned as a :class:`dimod.BinaryQuadraticModel` object.

    :return: qubo as dimod.BinaryQuadraticModel object
    :rtype: dimod.BinaryQuadraticModel
    """

    try:
        import dimod
    except Exception as oops:
        print('\n\n' + (100 * '#'))
        print('pip install dwave-ocean-sdk')
        print((100 * '#') + '\n\n')
        raise oops

    return dimod.BinaryQuadraticModel(
        {i0: self._p1[i0] for i0 in self._p1},
        {(i0, i1): self._p2[i0][i1] for i0 in self._p2 for i1 in self._p2[i0]},
        self._p0,
        dimod.BINARY)


In [ ]:
bqm_problem=HQ.as_bqm()

In [ ]:
os.environ['DWAVE_API_TOKEN']='YOUR TOKEN'

## Hybrid Solver

In [ ]:
from dimod.generators import and_gate
from dwave.system import LeapHybridSampler

sampler = LeapHybridSampler()    
answer = sampler.sample(bqm_problem)   
print(answer)  

In [ ]:
for datum in answer.data(['sample', 'energy']):     
   print(datum.sample, datum.energy)

In [ ]:
solution_dwave=list(datum.sample.values())

In [ ]:
print( "HQ  = %10.6f" % (HQ.compute(solution_dwave)) )
print( "H_1 = %10.6f" % (H_1.compute(solution_dwave)) )
print( "H_2 = %10.6f" % (H_2.compute(solution_dwave)) )

## Purely Quantum Solver

In [ ]:
from dwave.system.composites import EmbeddingComposite
from dwave.system.samplers import DWaveSampler
sample_time = time.time()

# Set a QPU sampler
sampler = EmbeddingComposite(DWaveSampler())

num_reads = 2000
sampleset = sampler.sample(bqm_problem,
                               num_reads=num_reads,
                               label='Purely Quantum Exec')

In [ ]:
for datum in sampleset.lowest().data(['sample', 'energy']):     
   print(datum.sample, datum.energy)

In [ ]:
solution_dwave=list(datum.sample.values())

In [ ]:
print( "HQ  = %10.6f" % (HQ.compute(solution_dwave)) )
print( "H_1 = %10.6f" % (H_1.compute(solution_dwave)) )
print( "H_2 = %10.6f" % (H_2.compute(solution_dwave)) )